In [1]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
  tf.app.run()


Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-u

INFO:tensorflow:probabilities = [[0.09071059 0.09466582 0.09883225 0.10235545 0.10317245 0.10116375
  0.10740571 0.1005643  0.09418192 0.10694773]
 [0.09628812 0.09588653 0.10034157 0.10127401 0.09497967 0.09829356
  0.10400131 0.10255899 0.09883419 0.10754208]
 [0.09280385 0.08964169 0.10197602 0.09530786 0.09327745 0.10616966
  0.10943796 0.10287765 0.1005069  0.1080009 ]
 [0.09284244 0.10517549 0.09187622 0.0929706  0.09472215 0.10856596
  0.10278379 0.11543359 0.10286982 0.09275993]
 [0.09741243 0.10044584 0.10839228 0.09950344 0.09927856 0.09888654
  0.09792271 0.1020951  0.09514157 0.10092147]
 [0.092315   0.09814071 0.10209301 0.09757616 0.09877837 0.09728337
  0.10299192 0.10195386 0.10372215 0.10514549]
 [0.09396815 0.09343103 0.09425368 0.11057138 0.10664973 0.10124185
  0.09507901 0.10110367 0.1009123  0.10278922]
 [0.09037112 0.09982861 0.10232116 0.09715168 0.09444311 0.10466674
  0.10004725 0.0991166  0.09808477 0.11396892]
 [0.10060363 0.08989891 0.09855175 0.11422023 0.

INFO:tensorflow:probabilities = [[0.09707322 0.09697085 0.1002778  0.10580093 0.09569722 0.0965137
  0.09864632 0.0990849  0.10013808 0.10979699]
 [0.09730806 0.10324977 0.10016043 0.10425195 0.09469046 0.10592407
  0.09851182 0.0911302  0.09619348 0.10857975]
 [0.09325358 0.08606489 0.0958406  0.10372987 0.09791761 0.09493901
  0.10510927 0.10366902 0.10869227 0.11078384]
 [0.09306376 0.09401973 0.10282961 0.09881581 0.09806854 0.1038648
  0.09847187 0.09461424 0.10668647 0.10956522]
 [0.09632796 0.09607625 0.10558945 0.10411856 0.09816582 0.10588995
  0.09981947 0.09644183 0.09614842 0.10142224]
 [0.09746626 0.08988891 0.10582341 0.11049399 0.10223354 0.10678685
  0.0851322  0.09167803 0.1047527  0.10574416]
 [0.10490578 0.09160365 0.10116676 0.10810101 0.10261916 0.09446371
  0.10346079 0.10099147 0.09351003 0.0991777 ]
 [0.09531998 0.1010311  0.10274014 0.10313764 0.09761333 0.09926425
  0.10308108 0.10239795 0.0952776  0.10013694]
 [0.10422729 0.09184921 0.10021567 0.10418335 0.08

INFO:tensorflow:probabilities = [[0.09194417 0.08586211 0.09466155 0.103112   0.0999525  0.09516952
  0.10416951 0.1080197  0.09744566 0.11966328]
 [0.09872011 0.1028057  0.09310018 0.10235553 0.09747198 0.09908964
  0.09110615 0.0995388  0.10769655 0.10811535]
 [0.09367651 0.08999206 0.10000904 0.11067128 0.09975833 0.10191061
  0.11253744 0.0942858  0.10113201 0.09602692]
 [0.09906562 0.09102309 0.09415525 0.10416877 0.10259175 0.10571385
  0.10242229 0.09358486 0.09938885 0.10788568]
 [0.08974914 0.09762547 0.09920897 0.10223817 0.09147255 0.10344514
  0.09966293 0.09676214 0.10969505 0.11014041]
 [0.10183313 0.09111939 0.10332656 0.10713593 0.09453356 0.10482223
  0.10547307 0.0953019  0.10311452 0.09333979]
 [0.09582467 0.09540402 0.11150824 0.10692495 0.09989035 0.0904608
  0.0965564  0.09516464 0.09965042 0.10861547]
 [0.09032498 0.09090519 0.11213706 0.10478642 0.09304564 0.10028414
  0.09653276 0.10312634 0.1102672  0.09859025]
 [0.09342643 0.09304496 0.10190047 0.09951112 0.0

INFO:tensorflow:probabilities = [[0.09904232 0.08125022 0.11077705 0.11355171 0.09914812 0.10362831
  0.08972798 0.10490108 0.09788743 0.1000858 ]
 [0.09831622 0.0962621  0.09535823 0.10439    0.09852865 0.10427672
  0.09827103 0.10745835 0.09102961 0.10610905]
 [0.09551446 0.09771048 0.09900256 0.08650359 0.09560245 0.09396069
  0.11404464 0.11088945 0.09181004 0.11496165]
 [0.09901128 0.09410791 0.0968395  0.0945988  0.10214102 0.09723359
  0.09881373 0.09223638 0.10512148 0.11989629]
 [0.0939344  0.1006123  0.10731608 0.10376136 0.0950145  0.10325667
  0.09270391 0.10107765 0.09221159 0.11011153]
 [0.10039686 0.08951963 0.10181558 0.1138225  0.08528635 0.10626487
  0.0992079  0.09194113 0.11404897 0.09769617]
 [0.09965747 0.08741215 0.10905765 0.09520165 0.09812585 0.09678395
  0.10040508 0.10568461 0.10103002 0.10664157]
 [0.09823106 0.1041853  0.0977065  0.10201356 0.09562136 0.09618798
  0.09917195 0.09563326 0.11122984 0.10001924]
 [0.08556784 0.10786092 0.09589335 0.09443014 0.

...

INFO:tensorflow:probabilities = [[0.00000104 0.99297696 0.00005028 0.00010914 0.00005577 0.00017706
  0.0003422  0.00001083 0.00619824 0.00007842]
 [0.00054526 0.00080257 0.12690543 0.00016141 0.26722315 0.01019965
  0.5860542  0.00045173 0.00042904 0.00722753]
 [0.00000289 0.00000008 0.99993956 0.00004563 0.00000004 0.00000016
  0.         0.00000005 0.00001155 0.00000006]
 [0.00000101 0.99961734 0.00008867 0.00000778 0.00001136 0.00000097
  0.00000696 0.00017762 0.00008102 0.00000742]
 [0.00000001 0.00000002 0.00000047 0.00000036 0.9997633  0.00000069
  0.00000067 0.0000425  0.00000034 0.00019163]
 [0.00004041 0.99661106 0.00053134 0.00023135 0.00013847 0.00000352
  0.00011142 0.00084095 0.00138702 0.00010443]
 [0.00000076 0.00000008 0.00000178 0.00036074 0.00000021 0.99961555
  0.00000006 0.00000029 0.00000415 0.0000164 ]
 [0.00005514 0.00031355 0.00011562 0.00144095 0.00200429 0.08229237
  0.0014828  0.00001033 0.91216135 0.00012366]
 [0.00215658 0.01181104 0.00722494 0.34354347 0.

INFO:tensorflow:probabilities = [[0.00002039 0.99817395 0.00010797 0.00008582 0.00025605 0.00002845
  0.00002642 0.00009915 0.00107344 0.00012834]
 [0.00000078 0.00000933 0.0000305  0.9993074  0.00000011 0.000623
  0.00000014 0.00000006 0.000027   0.00000165]
 [0.00000128 0.00000004 0.00002508 0.00000186 0.00000038 0.99945873
  0.00003497 0.         0.00047717 0.0000005 ]
 [0.99992776 0.00000002 0.0000206  0.00000049 0.00000052 0.00000316
  0.00002675 0.00000025 0.00000513 0.00001539]
 [0.00264543 0.00030276 0.00937766 0.00216222 0.00321598 0.9494004
  0.00663837 0.00553763 0.01381415 0.00690546]
 [0.00003202 0.00006604 0.00024686 0.00000152 0.0004784  0.00004368
  0.9990194  0.00000011 0.00011182 0.00000014]
 [0.00000108 0.00000008 0.00000092 0.00000048 0.9998472  0.00007513
  0.00001235 0.000011   0.00000235 0.00004944]
 [0.00000503 0.00000005 0.00002306 0.00902223 0.00000691 0.986598
  0.         0.00011526 0.00054485 0.0036846 ]
 [0.         0.         0.00001603 0.99997103 0.00000

INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-05-24-03:58:42
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9686, global_step = 20000, loss = 0.10151006
{'loss': 0.10151006, 'global_step': 20000, 'accuracy': 0.9686}


SystemExit: ignored

/usr/local/lib/python2.7/dist-packages/IPython/core/interactiveshell.py:2890: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
